In [95]:
import json
import requests
import praw
import numpy

reddit = praw.Reddit(client_id='tiBit4kBeuoOTA', 
                     client_secret='7-HPDa9q92MS0a-AnUVYb72QDzU', 
                     user_agent='TorkilSamStat', 
                     username='TorkSamStat', 
                     password='bbybbyduerinnafor')

# STATIC VARIABLES
base_url = 'https://api.pushshift.io/reddit/search/comment/'
wanted_count_auth = 5
wanted_count_sub = 5
unwanted_users = ["[deleted]", "AutoModerator"]
unwanted_count = len(unwanted_users)

    
# FUNCTIONS
def getKeysFromDict(data):
    users = []
    for obj in data:
        if obj['key'] not in unwanted_users:
            users.append(obj['key'])
    return users

def getMostActiveAuthorsInSubReddit(subreddit):
    #if subreddit in used_subreddits:
    #    return []
    #else:
    url = base_url + '?since=100d&subreddit={}&aggs=author&agg_size={}'.format(subreddit, wanted_count_auth + unwanted_count)
    response_raw = requests.get(url)
    print(url, response_raw)
    response = response_raw.json()
    print(response)
    fetched_authors = getKeysFromDict(response['aggs']['author'])
    print("*******************")
    print()
    return fetched_authors

def getMostActiveSubRedditForAuthor(author):
    #if author in used_authors:
    #    return []
    #else:
    url = base_url + '?since=100d&author={}&aggs=subreddit&agg_size={}'.format(author, wanted_count_sub)
    response_raw = requests.get(url)
    print(url, response_raw)
    response = response_raw.json()
    print(response)
    fetched_subreddits = getKeysFromDict(response['aggs']['subreddit'])
    for sub in used_subreddits:
            if (sub not in used_subreddits):
                used_subreddits.append(sub)
    print("*******************")
    print()
    return fetched_subreddits

In [ ]:
%%time
# Global variables
used_subreddits = []
used_authors = []


def get_relations(relational_array, subreddit, wanted_subcount):
    
    if wanted_subcount == 0:
        return []
    
    # Add subreddit to used_subreddits
    used_subreddits.append(subreddit)
    
    # Retrieve users from subreddit
    users = getMostActiveAuthorsInSubReddit(subreddit)
    
    # Retrieve subs from active users in subreddit
    for user in users:
        if user not in used_authors:
            subs = getMostActiveSubRedditForAuthor(user)
            used_authors.append(user)
            
            # Enter new level
            for sub in subs:
                if sub != subreddit:
                    relational_array.append([subreddit, sub])
                if sub not in used_subreddits:
                    relational_array.extend(get_relations([], sub, wanted_subcount - 1))
                    
    return relational_array


rels = get_relations([], 'The_Donald', 5)
rels

https://api.pushshift.io/reddit/search/comment/?since=100d&subreddit=The_Donald&aggs=author&agg_size=7 <Response [200]>
{'aggs': {'author': [{'doc_count': 35028, 'key': 'AutoModerator'}, {'doc_count': 21329, 'key': '[deleted]'}, {'doc_count': 1327, 'key': 'mangoroti'}, {'doc_count': 1077, 'key': 'PropellerPowerCurve'}, {'doc_count': 961, 'key': 'ENVYNITAZ'}, {'doc_count': 853, 'key': 'thenew23rd'}, {'doc_count': 708, 'key': 'MAGA_MAGGING_MAGA'}]}, 'data': [{'all_awardings': [], 'associated_award': None, 'author': 'Purplepunch36', 'author_flair_background_color': '', 'author_flair_css_class': 'illinois', 'author_flair_richtext': [], 'author_flair_template_id': None, 'author_flair_text': 'IL', 'author_flair_text_color': 'dark', 'author_flair_type': 'text', 'author_fullname': 't2_in26u', 'author_patreon_flair': False, 'author_premium': False, 'awarders': [], 'body': 'Why alienate any side of your customer base? Losing sales because of virtue signaling seems like a dumb fucking idea.', 'co

### 